![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 6,7. <i>Preprocessing i postprocessing</i> [laboratoria]</h2>
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Na dzisiejszych zajęciach zajmiemy się niezwykle przydatnymi narzędziami wspomagającymi pracę tłumacza. W odróżnieniu od dotychczas poznanych, nie są one oparte na pamięci tłumaczeń, ani na słownikach. Chodzi o techniki preprocessingu i postprocessingu.

Proces tłumaczenia przeprowadzony w pełni profesjonalnie składa się z wielu faz, które angażują nie tylko tłumaczy, ale także kierowników projektu, analityków, czy korektorów. Każda z tych osób do swojej pracy może wykorzystywać system informatyczny, do którego na początku całego procesu trafiają pliki do tłumaczenia. Oznacza to, że zanim tekst źródłowy trafi do tłumacza, system ma jeszcze szansę coś w nim zmienić. A kiedy tłumacz wykona już swoją pracę, można uruchomić kolejny mechanizm, który zmodyfikuje tłumaczenie przed oddaniem go do zamawiającego. Jak się domyślamy, modyfikacje tekstu przed przekazaniem go do tłumacza nazywamy **preprocessingiem**, natomiast te dokonywane po wykonaniu tłumaczenia (ale przed zwróceniem go do klienta) nazywamy **postprocessingiem**. Terminy te, będące mało zgrabnymi kalkami z języka angielskiego, mają wersje prawdziwie polskie: przetwarzanie wstępne i końcowe. Wersje te są jednak stosowane na tyle rzadko, że mogą jedynie wprowadzić zamieszanie (co w gruncie rzeczy jest dość smutne).

Typowe operacje w fazie preprocessingu obejmują:
* identyfikację tagów xmlowych (które często są później wyświetlane w interfejsie CAT-a jako jeden niepodzielny znak)
* identyfikację segmentów, których nie należy tłumaczyć (na przykład składających się z samych liczb)

* identyfikację dat i jednostek miary w tekście źródłowym

We wszystkich tych operacjach niezwykle przydatne okazują się wyrażenia regularne.

### Ćwiczenie 1: Używając wyrażeń regularnych napisz funkcję do znajdowania wszystkich tagów XML w tekście. Funkcja powinna zwracać pozycje, na których znalazła tagi.

In [ ]:
import re

def find_tags(text):
    pattern = r'</?[\w:.-]+[^>]*>'
    matches = re.finditer(pattern, text)
    return [(match.group(), match.start(), match.end()) for match in matches]

In [ ]:
xml = "<note><to>Tove</to><from>Jani</from><heading>Reminder</heading><body>Don't forget me this weekend!</body></note>"
print(find_tags(xml))

[('<note>', 0, 6), ('<to>', 6, 10), ('</to>', 14, 19), ('<from>', 19, 25), ('</from>', 29, 36), ('<heading>', 36, 45), ('</heading>', 53, 63), ('<body>', 63, 69), ('</body>', 98, 105), ('</note>', 105, 112)]


### Ćwiczenie 2: Używając wyrażeń regularnych napisz funkcję do identyfikacji segmentów, których nie należy tłumaczyć. Zastosuj wymyślone przez siebie kryteria. Funkcja is_translatable powinna zwracać True, jeśli segment powinien być przetłumaczony przez tłumacza (zwykłe zdanie). False powinno być zwrócone, kiedy segment jest nieprzetłumaczalny i powinien zostać skopiowany (np. 4.2.1.)

In [ ]:
def is_translatable(text):
    version_pattern = r'^\d+(\.\d+)+$'  # numery wersji np. 1.2.3
    url_pattern = r'https?://[\w.-]+'  # URL (http|https)://example.com
    email_pattern = r'[\w.-]+@[\w.-]+\.\w+'  # cos@gmail.com

    if re.match(version_pattern, text) or re.match(url_pattern, text) or re.match(email_pattern, text):
      return False
    return True

In [ ]:
print(is_translatable("1.2.3"))
print(is_translatable("http://example.com"))
print(is_translatable("example@example.com"))
print(is_translatable("cos@gmail.com"))
print(is_translatable("To jest zwykłe zdanie."))

False
False
False
False
True


### Ćwiczenie 3: Używając wyrażeń regularnych napisz funkcję do identyfikacji i interpretacji 5 wybranych przez siebie formatów daty. Funkcja powinna zwracać pozycje, na których odnalazła daty oraz dzień, miesiąc i rok, które ta data reprezentuje.

In [ ]:
def find_dates(text):
    month_to_number = {
        'January': 1,
        'February': 2,
        'March': 3,
        'April': 4,
        'May': 5,
        'June': 6,
        'July': 7,
        'August': 8,
        'September': 9,
        'October': 10,
        'November': 11,
        'December': 12
    }

    date_patterns = [
        (r'(\d{2})/(\d{2})/(\d{4})', lambda x: (int(x[0]), int(x[1]), int(x[2])), 'dd/mm/yyyy'), # dd/mm/yyyy
        (r'(\d{2})-(\d{2})-(\d{4})', lambda x: (int(x[1]), int(x[0]), int(x[2])), 'mm-dd-yyyy'), # mm-dd-yyyy
        (r'(\d{4})\.(\d{2})\.(\d{2})', lambda x: (int(x[2]), int(x[1]), int(x[0])), 'yyyy.mm.dd'), # yyyy.mm.dd
        (r'(\d{2}) (\w+), (\d{4})', lambda x: (int(x[0]), month_to_number[x[1]], int(x[2])), 'dd Month, yyyy'), # dd Month, yyyy
        (r'(\d{4})/(\d{2})/(\d{2})', lambda x: (int(x[2]), int(x[1]), int(x[0])), 'yyyy/mm/dd')  # yyyy/mm/dd
    ]

    results = []
    for pattern, parser, format_name in date_patterns:
        for match in re.finditer(pattern, text):
            day, month, year = parser(match.groups())
            results.append((match.span(), day, month, year, format_name))

    return results

In [ ]:
text_example = "Spotkanie odbędzie się 31/12/2020, inna data to 12-31-2020 oraz konferencja 2020.12.31, urlop 31 December, 2020 i wpis 2020/12/31."
print(find_dates(text_example))

[((23, 33), 31, 12, 2020, 'dd/mm/yyyy'), ((48, 58), 31, 12, 2020, 'mm-dd-yyyy'), ((76, 86), 31, 12, 2020, 'yyyy.mm.dd'), ((94, 111), 31, 12, 2020, 'dd Month, yyyy'), ((119, 129), 31, 12, 2020, 'yyyy/mm/dd')]


Po preprocessingu i tłumaczeniu czas na postprocessing. Ponieważ wykonywany jest on na przetłumaczonym tekście, jego głównym zadaniem jest eliminacja błędów popełnionych przez tłumacza w fazie tłumaczenia. Podczas postprocessingu najczęściej wykonuje się:
* korektę pisowni dla języka docelowego
* usuwanie błędów typograficznych z tekstu (np. wielokrotne spacje, brak spacji po przecinku)
Stanowi to bardzo ważne wsparcie dla edytorów i korektorów, czyli osób sprawdzających pracę tłumacza.

Jednak nowoczesne CAT-y potrafią coś jeszcze. Są w stanie w sprytny sposób wykorzystać kombinację pre- i postprocessingu do wyręczenia tłumacza w żmudnych i technicznych czynnościach. Wykonajmy następujące ćwiczenie:

### Ćwiczenie 4: Wykorzystując funkcję find_dates napisz funkcję do obsługi dat w tłumaczeniu. Wejściem jest segment źródłowy oraz docelowy, które zawierają daty, przy czym daty te mogą być w różnych formatach. Dodatkowym parametrem wejściowym jest nazwa oczekiwanego formatu daty w tłumaczeniu (np. "Europe", "US", "digit-dot". Funkcja najpierw sprawdza, czy liczba dat w tłumaczeniu zgadza się z liczbą dat w segmencie źródłowym oraz czy odpowiadające sobie daty wskazują na ten sam dzień. Jeśli nie, wypisywane jest stosowne ostrzeżenie. Oczekiwanym wyjściem jest segment docelowy, w którym wszystkie daty są w żądanym formacie.

In [ ]:
def correct_dates(source_segment, target_segment, date_format):
    format_map = {
        "dd/mm/yyyy": "{2:02d}/{1:02d}/{0:04d}",
        "mm-dd-yyyy": "{1:02d}-{2:02d}-{0:04d}",
        "yyyy.mm.dd": "{0:04d}.{1:02d}.{2:02d}",
        "dd Month, yyyy": "{2:02d} {1:02d}, {0:04d}",
        "yyyy/mm/dd": "{0:04d}/{1:02d}/{2:02d}"
    }

    source_dates = find_dates(source_segment)
    target_dates = find_dates(target_segment)

    if len(source_dates) != len(target_dates):
        print("Warning: Number of dates in source and target texts do not match.")

    for s, t in zip(source_dates, target_dates):
        if (s[1], s[2], s[3]) != (t[1], t[2], t[3]):
            print("Warning: Dates do not correspond to the same day.")
            break

    new_target_text = target_segment
    replacements = [(t[0], format_map[date_format].format(t[3], t[2], t[1])) for t in target_dates]

    for span, new_date in reversed(replacements):
        new_target_text = new_target_text[:span[0]] + new_date + new_target_text[span[1]:]

    return new_target_text

In [ ]:
source = "Data spotkania to 2020.12.30."
target = "The meeting date is 12-31-2020."
print(correct_dates(source, target, "yyyy/mm/dd"))

The meeting date is 2020/12/31.


Co jeszcze można zrobić? Zajmijmy się tagami XML. Z punktu widzenia tłumacza najlepiej byłoby, gdyby mógł przetłumaczyć segment źródłowy zawierający tagi XML na język docelowy zupełnie ignorując te tagi. Ponieważ jednak tagi muszą jakoś znaleźć się w segmencie docelowym, przydałaby się jakaś "magiczna różdżka", która przeniosłaby wszystkie tagi ze źródła do tłumaczenia na mniej więcej dobre miejsca. Spełnijmy marzenie tłumacza!

Rozważmy następujący algorytm: na wejściu mamy segment źródłowy zawierający tagi oraz segment docelowy bez tagów. Dokonujemy tokenizacji segmentu źródłowego tak, aby tagi były osobnymi tokenami. Następnie przeprowadźmy tokenizację segmentu docelowego. Gdy to jest gotowe, możemy zabrać się za przenoszenie (kopiowanie) tagów z segmentu źródłowego do docelowego.

![Transfer tagów](img/tagtransfer.png)

Gdzie w segmencie docelowym powinien trafić tag? Przede wszystkim pomiędzy tokeny - nie chcemy rozbijać słów tagami. Pytanie tylko, pomiędzy które tokeny? Jeśli sytuacja jest taka, jak powyżej, kiedy segment źródłowy i docelowy mają taką samą liczbę słów nie będących tagami, przenosimy tagi na odpowiadające pozycje w tłumaczeniu. Natomiast jeśli długość tłumaczenia jest inna niż źródła, należy obliczać te pozycje w sposób proporcjonalny - jeśli np. mamy tag w źródle na pozycji 3, a tłumaczenie jest dwa razy dłuższe niż źródło, tag powinien być przeniesiony do tłumaczenia na pozycję 6. W przypadku niecałkowitych wartości proporcji stosujemy zaokrąglenia.

### Ćwiczenie 5: Zaimplementuj opisany algorytm transferu tagów.

In [ ]:
import re

def tokenize(text):
    if not isinstance(text, str):
        raise ValueError("Tekst musi być typu string")
    tokens = re.split(r'(\s+|<[^>]+>)', text)

    return [token for token in tokens if token.strip()]

def map_tags(source_tags, source_length, target_length):
    mapped_indices = []
    for index, tag in source_tags:
        mapped_index = int(round((index / source_length) * target_length))
        mapped_indices.append((mapped_index, tag))
    return mapped_indices

def insert_tags(target_tokens, tags):
    for index, tag in sorted(tags, reverse=True):  # Wstawianie od tyłu, aby nie zaburzać indeksów
        target_tokens.insert(index, tag)
    return target_tokens

In [ ]:
def transfer_tags(source_segment, target_segment):
    if not isinstance(source_segment, str) or not isinstance(target_segment, str):
        raise ValueError("Oba teksty muszą być typu string")

    source_tokens = tokenize(source_segment)
    target_tokens = tokenize(target_segment)

    source_tags = find_tags(source_tokens)
    source_length = len([t for t in source_tokens if not t.startswith('<')])
    target_length = len(target_tokens)

    mapped_tags = map_tags(source_tags, source_length, target_length)

    return ' '.join(insert_tags(target_tokens, mapped_tags))

In [ ]:
source = "Here is <b>bold</b> text and <i>italic</i> text."
target = "Oto tekst pogrubiony i tekst pochylony."

print(transfer_tags(source, target))

Oto tekst <b> pogrubiony </b> i tekst pochylony. <i> </i>
